In [1]:
##

import scrapy
from scrapy.crawler import CrawlerProcess
import pandas
import json
from scrapy.item import Item, Field
import time
import random

# Creamos la araña.
class uoc_spider(scrapy.Spider):

    # Asignamos un nombre a la araña.
    name = "uoc_spider"

    # Indicamos la url que queremos analizar en primer lugar.
    start_urls = [
        "https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films"
    ]

    custom_settings = {
        'FEEDS': { 'data_wiki.json': {'format': 'json', 'overwrite': True, 'encofing':'utf-8'}}
        }

           # Definimos el analizador.
            
    def parse(self, response):
        # Extraemos la info de la película
        for name in response.xpath('//table[@class="wikitable sortable"]//tr'):
            time.sleep(random.uniform(0.20, 0.70))
            # Capturamos las películas ganadoras
            if name.xpath('.//b').get() is not None:
                best_movie = True
            else:
                best_movie = False
            yield {
               'title': name.xpath('.//i//text()').get(),
               'year': name.xpath('(.//a)[2]/text()').get(),
               'best movie': best_movie,
               'awards': name.xpath('(./td)[3]/text()').get(),
               'nominations': name.xpath('(./td)[4]/text()').get(),
               'linkMovie': str(name.xpath('.//i//a/@href').get())

            }       
        
        # Iteramos sobre los links
        for item in response.xpath('//table[@class = "wikitable sortable"]//i//a/@href'):
            time.sleep(random.uniform(0.20, 0.70))
            if item is not None:
                yield response.follow(item.get(), callback=self.parse_movies)
                
            
     # Capturamos la información de cada película
    def parse_movies(self, response):
        response_type = ['"Directed"', '"Screenplay"', 
                         '"Starring"', '"Produced"', 
                         "'Cinematography'", "'Edited'",
                         "'Music'", "'Production company'",
                         "'Distributed'", "'Release dates'",
                         "'Running time'", "'Country'",
                         "'Language'", "'Budget'",
                         "'Box office'"
                        ]
        for tipo in response_type:
            path_template = '//table[@class="infobox vevent"]//th[contains(text(), {})]/following-sibling::td'.format(tipo)
            if response.xpath(path_template+'//ul').get() is not None:
                path_template = path_template+'//li'
            for name in response.xpath(path_template):
                yield {'movie': response.xpath('//h1[@id="firstHeading"]/i/text()').get(),
                       tipo: name.xpath('.//text()').get(),
                       'link': response.request.url,
                    }



        # Links de los actores
        path_template = '//table[@class="infobox vevent"]//th[contains(text(), "Starring")]/following-sibling::td'
        if response.xpath(path_template+'//ul').get() is not None:
            path_template = path_template+'//li'
        
        for item in response.xpath(path_template+'//@href'):
            if item is not None:
                yield response.follow(item.get(), callback=self.parse_cast)
                time.sleep(random.uniform(0.20, 0.70))
                
            
     # Capturamos la información de cada persona
    def parse_cast(self, response):
        time.sleep(random.uniform(0.20, 0.70))
        
        # Loop para determinar el género de la persona
        females_sum = 0
        males_sum = 0
        female_list = ['" her "', '"Her "', 
                       '" she "', '"She "', 
                       '" female "', 
                       '" actress "', 
                       '" woman "']
        male_list = ['" his "', '"His "', 
                     '" he "', '"He "', 
                     '" male "', 
                     '" man "']

        
        if response.xpath('//div[@class="catlinks"]//a[contains(text(), "women") or contains(text(), "actresses") or contains(text(), "females")]').get() is not None:
            female = True
        elif response.xpath('//div[@class="catlinks"]//a[contains(text(), "men") or contains(text(), "actors") or contains(text(), "males")]').get() is not None:
            female = False 
        else:
            for e in response.xpath('//p'):
                for word_fem in female_list:
                    path = 'count(.//text()[contains(.,{})])'.format(word_fem)
                    females_sum = females_sum + float(e.xpath(path).get())
                    
                for word_male in male_list:
                    path = 'count(.//text()[contains(., {})])'.format(word_male)
                    males_sum = males_sum + float(e.xpath(path).get())

            if females_sum > males_sum:
                female = True
            elif females_sum < males_sum:
                female = False
            else:
                female = 'NA'

            
        yield {'name': response.xpath('//table[@class="infobox biography vcard"]//tr//div[@class="fn"]/text()').get(),
               'female': female,
              'birthdate': response.xpath('//table[@class="infobox biography vcard"]//tr//span[@class="bday"]/text()').get(),
               #Birthplace sale regular
               'birthplace': response.xpath('//table[@class="infobox biography vcard"]//tr//div[@class="birthplace"]//text()').getall(),
               'link': response.request.url
              }
                     
            
if __name__ == "__main__":
# Creamos un crawler
  process = CrawlerProcess({'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)',
                    'DOWNLOAD_HANDLERS': {'s3': None},
                    'LOG_ENABLED': True
                })

# Inicializamos el crawler con nuestra araña.
process.crawl(uoc_spider)

                # Lanzamos la araña
process.start()

2022-11-08 15:26:22 [scrapy.utils.log] INFO: Scrapy 2.6.1 started (bot: scrapybot)
2022-11-08 15:26:22 [scrapy.utils.log] INFO: Versions: lxml 4.6.3.0, libxml2 2.9.12, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 22.4.0, Python 3.9.7 (default, Sep 16 2021, 08:50:36) - [Clang 10.0.0 ], pyOpenSSL 21.0.0 (OpenSSL 1.1.1l  24 Aug 2021), cryptography 3.4.8, Platform macOS-10.16-x86_64-i386-64bit
2022-11-08 15:26:22 [scrapy.crawler] INFO: Overridden settings:
{'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'}
2022-11-08 15:26:22 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.selectreactor.SelectReactor
2022-11-08 15:26:22 [scrapy.extensions.telnet] INFO: Telnet Password: 7b2f8e64ea0ab47e
2022-11-08 15:26:22 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusage.MemoryUsage',
 'scrapy.extensions.feedexport.FeedExporter',
 'scrapy.extensions.logstats.LogS

2022-11-08 15:26:32 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'The Father', 'year': '2020', 'best movie': False, 'awards': '2', 'nominations': '6\n', 'linkMovie': '/wiki/The_Father_(2020_film)'}
2022-11-08 15:26:32 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Judas and the Black Messiah', 'year': '2020', 'best movie': False, 'awards': '2', 'nominations': '6\n', 'linkMovie': '/wiki/Judas_and_the_Black_Messiah'}
2022-11-08 15:26:32 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Minari', 'year': '2020', 'best movie': False, 'awards': '1', 'nominations': '6\n', 'linkMovie': '/wiki/Minari_(film)'}
2022-11-08 15:26:33 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Mank', 'year': 

2022-11-08 15:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Green Book', 'year': '2018', 'best movie': True, 'awards': '3', 'nominations': '5\n', 'linkMovie': '/wiki/Green_Book_(film)'}
2022-11-08 15:26:45 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Bohemian Rhapsody', 'year': '2018', 'best movie': False, 'awards': '4', 'nominations': '5\n', 'linkMovie': '/wiki/Bohemian_Rhapsody_(film)'}
2022-11-08 15:26:45 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Roma', 'year': '2018', 'best movie': False, 'awards': '3', 'nominations': '10\n', 'linkMovie': '/wiki/Roma_(2018_film)'}
2022-11-08 15:26:46 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Black Panther', 'year': '2018', 

2022-11-08 15:26:59 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Flesh and Sand', 'year': '2017', 'best movie': False, 'awards': '0 (1)', 'nominations': '0\n', 'linkMovie': '/wiki/Flesh_and_Sand'}
2022-11-08 15:26:59 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Moonlight', 'year': '2016', 'best movie': True, 'awards': '3', 'nominations': '8\n', 'linkMovie': '/wiki/Moonlight_(2016_film)'}
2022-11-08 15:26:59 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'La La Land', 'year': '2016', 'best movie': False, 'awards': '6', 'nominations': '14\n', 'linkMovie': '/wiki/La_La_Land_(film)'}
2022-11-08 15:27:00 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Hacksaw Ridge', 'year': '2016',

2022-11-08 15:27:12 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Spectre', 'year': '2015', 'best movie': False, 'awards': '1', 'nominations': '1\n', 'linkMovie': '/wiki/Spectre_(2015_film)'}
2022-11-08 15:27:12 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Stutterer', 'year': '2015', 'best movie': False, 'awards': '1', 'nominations': '1\n', 'linkMovie': '/wiki/Stutterer_(film)'}
2022-11-08 15:27:13 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'Birdman or (The Unexpected Virtue of Ignorance)', 'year': '2014', 'best movie': True, 'awards': '4', 'nominations': '9\n', 'linkMovie': '/wiki/Birdman_(film)'}
2022-11-08 15:27:14 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films>
{'title': 'The Grand

...

2022-11-08 22:37:39 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/Craig_Sheffer>
{'name': 'Craig Sheffer', 'female': False, 'birthdate': '1960-04-23', 'birthplace': ['York, Pennsylvania', ', U.S.'], 'link': 'https://en.wikipedia.org/wiki/Craig_Sheffer'}
2022-11-08 22:37:40 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/Kim_Stanley>
{'name': 'Kim Stanley', 'female': True, 'birthdate': '1925-02-11', 'birthplace': ['Tularosa, New Mexico', ', U.S.'], 'link': 'https://en.wikipedia.org/wiki/Kim_Stanley'}
2022-11-08 22:37:40 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/Kristina_Adolphson>
{'name': 'Kristina Adolphson', 'female': True, 'birthdate': '1937-09-02', 'birthplace': ['Stockholm', ', Sweden'], 'link': 'https://en.wikipedia.org/wiki/Kristina_Adolphson'}
2022-11-08 22:37:41 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/Aladdin_(1992_Disney_film)>
{'movie': 'Aladdin

https://en.wikipedia.org/wiki/Aladdin_(1992_Disney_film)


2022-11-08 22:37:42 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/Aladdin_(1992_Disney_film)>
{'movie': 'Aladdin', "'Box office'": '$504.1\xa0million', 'link': 'https://en.wikipedia.org/wiki/Aladdin_(1992_Disney_film)'}
2022-11-08 22:37:42 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://en.wikipedia.org/wiki/Brenda_Blethyn> (referer: https://en.wikipedia.org/wiki/A_River_Runs_Through_It_(film))


https://en.wikipedia.org/wiki/Aladdin_(1992_Disney_film)


2022-11-08 22:37:42 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/Mats_Bergman>
{'name': 'Mats Bergman', 'female': False, 'birthdate': '1948-05-05', 'birthplace': ['Gothenburg', ', Sweden'], 'link': 'https://en.wikipedia.org/wiki/Mats_Bergman'}
2022-11-08 22:37:42 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://en.wikipedia.org/wiki/Emily_Lloyd> (referer: https://en.wikipedia.org/wiki/A_River_Runs_Through_It_(film))
2022-11-08 22:37:43 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://en.wikipedia.org/wiki/Jarl_Kulle> (referer: https://en.wikipedia.org/wiki/Fanny_and_Alexander)
2022-11-08 22:37:43 [scrapy.core.scraper] DEBUG: Scraped from <200 https://en.wikipedia.org/wiki/Brenda_Blethyn>
{'name': 'Brenda Blethyn', 'female': True, 'birthdate': '1946-02-20', 'birthplace': ['Ramsgate', ', ', 'Kent', ', England'], 'link': 'https://en.wikipedia.org/wiki/Brenda_Blethyn'}
2022-11-08 22:37:44 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://en.